In [12]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from itertools import combinations
from csv import DictWriter

from investigation_functions import  test_table_funcs as ttf
from investigation_functions import ml_funcs as mlf


In [ ]:
n_qubits_list = [4,8,16]
backends_list = ['brisbane','torino','fez','marrakesh']
circuits_list = ['1','2','3']
exp_type_list = ['Hardware', 'Simulation','Refreshed_Simulation']


In [ ]:

backend_pairs = list(combinations(backends_list, 2))
circuits_pairs =  list(combinations(circuits_list, 2))
exp_type_pairs =  list(combinations(exp_type_list, 2))

In [8]:
print("backends pairs:")
print(backend_pairs)
print("circuitspairs:")
print(circuits_pairs)
print("exp_type pairs:")
print(exp_type_pairs)

backends pairs:
[('brisbane', 'torino'), ('brisbane', 'fez'), ('brisbane', 'marrakesh'), ('torino', 'fez'), ('torino', 'marrakesh'), ('fez', 'marrakesh'), ('brisbane', 'brisbane'), ('torino', 'torino'), ('fez', 'fez'), ('marrakesh', 'marrakesh')]
circuitspairs:
[('1', '2'), ('1', '3'), ('2', '3'), ('1', '1'), ('2', '2'), ('3', '3')]
exp_type pairs:
[('Hardware', 'Simulation'), ('Hardware', 'Refreshed_Simulation'), ('Simulation', 'Refreshed_Simulation'), ('Hardware', 'Hardware'), ('Simulation', 'Simulation'), ('Refreshed_Simulation', 'Refreshed_Simulation')]


In [10]:
backend_same =list(zip(backends_list,backends_list))
circuit_same =list(zip(circuits_list,circuits_list))
exp_type_same=list(zip(exp_type_list,exp_type_list))

In [11]:
# for each thing that is different, the other 2 must be the same,
#but we must iterate through the other 2
# NB nr of qubits must always be the same

backends_vs_backends = []

row = []
for nr_qubits in n_qubits_list:
    

    for exp_type_pair in exp_type_same:
        

        for circuit_pair in circuit_same:
            

            for backend_pair in backend_pairs:
                row.append(nr_qubits)
                row.append(exp_type_pair)
                row.append(circuit_pair)
                row.append(backend_pair)
                backends_vs_backends.append(row)

print(backends_vs_backends)

[[4, ('Hardware', 'Hardware'), ('1', '1'), ('brisbane', 'torino'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('brisbane', 'fez'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('brisbane', 'marrakesh'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('torino', 'fez'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('torino', 'marrakesh'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('fez', 'marrakesh'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('brisbane', 'brisbane'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('torino', 'torino'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('fez', 'fez'), 4, ('Hardware', 'Hardware'), ('1', '1'), ('marrakesh', 'marrakesh'), 4, ('Hardware', 'Hardware'), ('2', '2'), ('brisbane', 'torino'), 4, ('Hardware', 'Hardware'), ('2', '2'), ('brisbane', 'fez'), 4, ('Hardware', 'Hardware'), ('2', '2'), ('brisbane', 'marrakesh'), 4, ('Hardware', 'Hardware'), ('2', '2'), ('torino', 'fez'), 4, ('Hardware', 'Hardware'), ('2', '2'), ('torino', 'marrakesh'), 4, ('Hardware', 'Hardware'), ('2', '2

In [31]:
def get_test_list(
        qubits_list,change,
        backends_list = ['brisbane','torino','fez','marrakesh'],
        circuits_list = ['1','2','3'],
        exp_type_list = ['Hardware', 'Simulated','Refreshed_Simulated']
    ):
    
    backend_same =list(zip(backends_list,backends_list))
    circuit_same =list(zip(circuits_list,circuits_list))
    exp_type_same=list(zip(exp_type_list,exp_type_list))

    exp_type_pairs_ = exp_type_same
    circuit_pairs_ = circuit_same
    backend_pairs_ = backend_same

    if change == 'exp_type':
        exp_type_pairs_ =  list(combinations(exp_type_list, 2))
    elif change == 'circuits':
        circuit_pairs_ =  list(combinations(circuits_list, 2))
    elif change == 'backends':
        backend_pairs_ = list(combinations(backends_list, 2))
    else:
        raise('invalid change variable')
    

    test_combos = []

    
    for exp_type_pair in exp_type_pairs_:
    
        for nr_qubits in qubits_list:

            for circuit_pair in circuit_pairs_:

                for backend_pair in backend_pairs_:

                    row = {
                        'exp_type_pair':exp_type_pair,
                        'nr_qubits':nr_qubits,
                        'circuit_pair':circuit_pair,
                        'backend_pair':backend_pair
                    }
                    test_combos.append(row)
    
    return test_combos
def get_df_file_path_from_row(test_row, dir_runs, df_nr = 1):
    index = df_nr-1
    nq = str(test_row['nr_qubits'])
    exp_t =test_row['exp_type_pair'][index]
    circ = str(test_row['circuit_pair'][index])

    #get csv file_name
    file_name = nq + "q_"
    if exp_t =='Hardware':
        file_name = file_name +"ibm_"+test_row['backend_pair'][index]
    else:
        file_name = file_name +"fake_"+test_row['backend_pair'][index]
    file_name = file_name +circ+".csv"

    #get file path
    file_path = dir_runs + exp_t +"_results/" 
    file_path = file_path+ nq+"q/"
    file_path = file_path + file_name

    return file_path


def load_test_dfs_from_test_row(test_row,dir_runs):
    df1_file_name = get_df_file_path_from_row(test_row,dir_runs,1)
    df2_file_name = get_df_file_path_from_row(test_row,dir_runs,2)

    df1 = pd.read_csv(df1_file_name)
    df2 = pd.read_csv(df2_file_name)

    return df1,df2

def get_and_record_corr_from_test_row(test_row, file_name,dir_corr,dir_runs):
    df1,df2 = load_test_dfs_from_test_row(test_row,dir_runs)
    corr_avg = df1.corrwith(df2).mean()
    
    fields = [
        "nr_qubits","exp_type 1","exp_type 2",
        "backend 1","backend 2","circuit 1","circuit 2",
        "corr avg"
    ]
    
    row = {
        "nr_qubits":test_row['nr_qubits'],
        "exp_type 1":test_row['exp_type_pair'][0],
        "exp_type 2":test_row['exp_type_pair'][1],
        "backend 1":test_row['backend_pair'][0],
        "backend 2":test_row['backend_pair'][1],
        "circuit 1":test_row['circuit_pair'][0],
        "circuit 2":test_row['circuit_pair'][1],
        "corr avg":corr_avg
    }
    with open(dir_corr+file_name, 'a', newline='') as f:
        writer = DictWriter(f, fieldnames=fields)
        writer.writerow(row)

def create_corr_csv(file_name,dir_corr):
    fields = [
        "nr_qubits","exp_type 1","exp_type 2",
        "backend 1","backend 2","circuit 1","circuit 2",
        "corr avg"
    ]
    with open(dir_corr+file_name, 'w', newline='') as f:
        writer = DictWriter(f, fieldnames=fields)
        writer.writeheader()

def get_and_record_corrs_from_tests_list(tests_list,file_name,dir_corr,dir_runs,create_csv = False):
    fields = [
        "nr_qubits","exp_type 1","exp_type 2",
        "backend 1","backend 2","circuit 1","circuit 2",
        "corr avg"
    ]
    if create_csv:
        create_corr_csv(file_name, dir_corr)
    
    for test_row in tests_list:
        get_and_record_corr_from_test_row(test_row,file_name,dir_corr,dir_runs)
    

In [38]:
dir_corr = "../Corr_results/testing/"
file_name = "8q_exp_type.csv"
dir_runs = "../"

qubits_list = [8]

tests_list_bvb = get_test_list(qubits_list, change = 'exp_type')
# create_corr_csv(file_name, dir_corr)
# print(tests_list_bvb[0]['exp_type_pair'][0])
# print(type(tests_list_bvb[0]['exp_type_pair'][0]))

# get_and_record_corr_from_test_row(
#     tests_list_bvb[0],file_name,dir_corr,dir_runs)

get_and_record_corrs_from_tests_list(
    tests_list_bvb,file_name,dir_corr,dir_runs,create_csv=True
)